In [1]:
import json
import numpy as np
import os
import torch
from torch.utils.data import Dataset, DataLoader
from torchvision import transforms, utils

from load_glove import Glove
from stanfordcorenlp import StanfordCoreNLP

In [2]:
# constants
train_file_raw = 'samples50000_0206194500.train.txt'
dev_file_raw = 'samples50000_0206194500.dev.txt'
test_file_raw = 'samples50000_0206194500.test.txt'
dataset_dir = './dataset_filtered'
train_file = '{}/train.json'.format(dataset_dir)
dev_file = '{}/dev.json'.format(dataset_dir)
test_file = '{}/test.json'.format(dataset_dir)
train_pos_file = '{}/train_pos.json'.format(dataset_dir)
dev_pos_file = '{}/dev_pos.json'.format(dataset_dir)
test_pos_file = '{}/test_pos.json'.format(dataset_dir)
train_dep_file = '{}/train_dep.json'.format(dataset_dir)
dev_dep_file = '{}/dev_dep.json'.format(dataset_dir)
test_dep_file = '{}/test_dep.json'.format(dataset_dir)

if not os.path.isdir(dataset_dir):
    os.mkdir(dataset_dir)

In [3]:
# ======================== initial dataset processing =====================

In [4]:
# load file
def ReadDataFile(filename):
    sentences = list()
    len_sentences = list()
    with open(filename, 'r', encoding='utf-8') as textfile:
        for line in textfile:
            line = line.strip()
            tokens = line.split()
            sentences.append(line)
            len_sentences.append(len(tokens))
    return sentences, len_sentences

In [5]:
# std and avg of sentence length in total dataset
sentences_tr, len_sentences_tr = ReadDataFile(train_file_raw)
sentences_dv, len_sentences_dv = ReadDataFile(dev_file_raw)
sentences_ts, len_sentences_ts = ReadDataFile(test_file_raw)

len_sentences_tt = len_sentences_tr + len_sentences_dv + len_sentences_ts
mean_total = np.mean(len_sentences_tt)
std_total = np.std(len_sentences_tt)

print(mean_total, std_total)

22.514047250226433 14.624483763629705


In [6]:
# filter sentences 
# take the sentences of length within range [mean - std, mean + std]
def FilterSentences(sentences, len_sentences, mean, std):
    filtered_sentences = list()
    for i in range(len(sentences)):
        if len_sentences[i] >= mean - std and len_sentences[i] <= mean + std:
            filtered_sentences.append(sentences[i])
    return filtered_sentences, len(filtered_sentences)

In [7]:
# num of sentences in raw dataset vs. num of sentences after [mean - std, mean + std] filter
sentences_tr, num_sentences_tr_flt = FilterSentences(sentences_tr, len_sentences_tr, mean_total, std_total)
sentences_dv, num_sentences_dv_flt = FilterSentences(sentences_dv, len_sentences_dv, mean_total, std_total)
sentences_ts, num_sentences_ts_flt = FilterSentences(sentences_ts, len_sentences_ts, mean_total, std_total)
print(len(len_sentences_tr), num_sentences_tr_flt)
print(len(len_sentences_dv), num_sentences_dv_flt)
print(len(len_sentences_ts), num_sentences_ts_flt)

with open(train_file, 'w', encoding='utf-8') as textfile:
    json.dump(sentences_tr, textfile, indent=2)

with open(dev_file, 'w', encoding='utf-8') as textfile:
    json.dump(sentences_dv, textfile, indent=2)

with open(test_file, 'w', encoding='utf-8') as textfile:
    json.dump(sentences_ts, textfile, indent=2)

277329 214804
36934 28148
40148 30134


In [8]:
# parsing with dependency parser
def DependencyParsing(sentences, num_sentences, out_pos_file_basename, out_dep_file_basename):
    file_index = 0
    current_min = 0
    sent_per_file = 10000
    current_max = min(sent_per_file, num_sentences - sent_per_file * file_index)
    
    sentences_with_pos = dict(zip(range(current_min, current_max), [[] for i in range(current_min, current_max)]))
    sentences_with_dep = dict(zip(range(current_min, current_max), [[] for i in range(current_min, current_max)]))
    
    stanfordnlp = StanfordCoreNLP('./stanford-corenlp-3.9.2') # initialize corenlp server in the background 
    properties = {'annotators': 'depparse', 'pipelineLanguage': 'en', 'outputFormat': 'json'}
    
    logging.info('annotating {} set with stanford parser, total sentences to annotate: {}...'.format(out_pos_file_basename[14:-4], num_sentences))
    
    for i in range(len(sentences)):
        annotated = stanfordnlp.annotate(sentences[i], properties=properties)
        
        annotated = json.loads(annotated)
        
        dep_info = annotated['sentences'][0]['enhancedPlusPlusDependencies']
        pos_info = annotated['sentences'][0]['tokens']
        
        sentences_with_dep[i] = dep_info
        
        
        for token in pos_info:
            sentences_with_pos[i].append({'index':token['index'], 'word':token['word'], 'pos':token['pos']})
        
        if (i + 1) % sent_per_file == 0 or i == len(sentences) - 1: # output a file after every so many sentences 
            logging.info('\t{}/{}: {}% parsed'.format((i+1), num_sentences, round((i+1)/num_sentences*100, 2)))

            out_pos_file = '{}.{}.json'.format(out_pos_file_basename, file_index)
            out_dep_file = '{}.{}.json'.format(out_dep_file_basename, file_index)
            
            with open(out_pos_file, 'w', encoding='utf-8') as textfile:
                json.dump(sentences_with_pos, textfile)
            
            with open(out_dep_file, 'w', encoding='utf-8') as textfile:
                json.dump(sentences_with_dep, textfile)
            
            # reset filename, range for the next batch  
            file_index += 1
            current_min = sent_per_file * file_index
            current_max = min(sent_per_file, num_sentences - sent_per_file * file_index) + sent_per_file * file_index
            
            sentences_with_pos = dict(zip(range(current_min, current_max), [[] for i in range(current_min, current_max)]))
            sentences_with_dep = dict(zip(range(current_min, current_max), [[] for i in range(current_min, current_max)]))
            
    stanfordnlp.close()

In [9]:
#### call dep parsing elsewhere

In [10]:
# ============================ Glove Part ==========================

In [11]:
glove_model = Glove()
glove_model.load_model(normalize=True)

Loading pretrained Glove vectors from file ./glove/glove.840B.300d.txt
  --9.11%  loaded.
  --18.21%  loaded.
  --27.32%  loaded.
  --36.43%  loaded.
  --45.54%  loaded.
  --54.64%  loaded.
  --63.75%  loaded.
  --72.86%  loaded.
  --81.97%  loaded.
  --91.07%  loaded.
Finished loading Glove model. 2196017 vectors loaded


In [12]:
# iterate over sentences (keep the index), filter out the sentences based on if token is in glove embedding or not
def FilterSentencesGlove(sentences, num_sentences, split_name):
    idx_sent_to_remove = list()
    for i in range(num_sentences):
        tokens = sentences[i].split()
        for w in tokens:
            if w == '-RCB-':
                w = ')'
            elif w == '-LCB-':
                w = '('
                
            if glove_model.get_vector(w) is None: 
                idx_sent_to_remove.append(i)
                break # if any of the token returns None, skip the sentence
    
    idx_sent_filtered = list(set(range(num_sentences)) - set(idx_sent_to_remove))
    
    with open('{}/{}_idx_filtered.txt'.format(dataset_dir, split_name), 'w', encoding='utf-8') as textfile:
        json.dump(idx_sent_filtered, textfile)
        
    return idx_sent_filtered

In [13]:
idx_sent_filtered_dv = FilterSentencesGlove(sentences_dv, num_sentences_dv_flt, 'dev')
idx_sent_filtered_ts = FilterSentencesGlove(sentences_ts, num_sentences_ts_flt, 'test')
idx_sent_filtered_tr = FilterSentencesGlove(sentences_tr, num_sentences_tr_flt, 'train')

Input token <Ewauna> is not in the model. Will return None type vector
Input token <heatsource> is not in the model. Will return None type vector
Input token <Brahdamba> is not in the model. Will return None type vector
Input token <Martanda> is not in the model. Will return None type vector
Input token <Martanda> is not in the model. Will return None type vector
Input token <Martanda> is not in the model. Will return None type vector
Input token <Diwan-in-Council> is not in the model. Will return None type vector
Input token <Martanda> is not in the model. Will return None type vector
Input token <Martanda> is not in the model. Will return None type vector
Input token <Martanda> is not in the model. Will return None type vector
Input token <Martanda> is not in the model. Will return None type vector
Input token <Endynomena> is not in the model. Will return None type vector
Input token <nine-fingered> is not in the model. Will return None type vector
Input token <73,744> is not in the 

Input token <Kundara> is not in the model. Will return None type vector
Input token <Alappad> is not in the model. Will return None type vector
Input token <Sakthikulangara> is not in the model. Will return None type vector
Input token <Mannathippara> is not in the model. Will return None type vector
Input token <Sasthamcotta> is not in the model. Will return None type vector
Input token <Katchai> is not in the model. Will return None type vector
Input token <Mantharan> is not in the model. Will return None type vector
Input token <Kurunkozhiyur> is not in the model. Will return None type vector
Input token <swimfins> is not in the model. Will return None type vector
Input token <swimfins> is not in the model. Will return None type vector
Input token <FDU2> is not in the model. Will return None type vector
Input token <FDU3> is not in the model. Will return None type vector
Input token <UWFP> is not in the model. Will return None type vector
Input token <KILOVOLT> is not in the model. 

Input token <Pomabamba> is not in the model. Will return None type vector
Input token <Fânețelor> is not in the model. Will return None type vector
Input token <al-Turkmani> is not in the model. Will return None type vector
Input token <al-Qurashi> is not in the model. Will return None type vector
Input token <AQI/ISI> is not in the model. Will return None type vector
Input token <massacre.For> is not in the model. Will return None type vector
Input token <AQI/ISI> is not in the model. Will return None type vector
Input token <Hanein> is not in the model. Will return None type vector
Input token <Batawi> is not in the model. Will return None type vector
Input token <led-government> is not in the model. Will return None type vector
Input token <l'Ahl> is not in the model. Will return None type vector
Input token <#FFC318> is not in the model. Will return None type vector
Input token <#FFC318> is not in the model. Will return None type vector
Input token <#FFC318> is not in the model. Wi

Input token <Karatgurk> is not in the model. Will return None type vector
Input token <Djurt-djurt> is not in the model. Will return None type vector
Input token <Karatgurk> is not in the model. Will return None type vector
Input token <second-brightest> is not in the model. Will return None type vector
Input token <Marshpillow> is not in the model. Will return None type vector
Input token <Gratiaen> is not in the model. Will return None type vector
Input token <Dileepa> is not in the model. Will return None type vector
Input token <Adprint> is not in the model. Will return None type vector
Input token <Tokár> is not in the model. Will return None type vector
Input token <508,714> is not in the model. Will return None type vector
Input token <breasts-and-blood> is not in the model. Will return None type vector
Input token <HOOK2> is not in the model. Will return None type vector
Input token <Okesene> is not in the model. Will return None type vector
Input token <Hitro> is not in the mo

Input token <Sharanskaya> is not in the model. Will return None type vector
Input token <uyezds> is not in the model. Will return None type vector
Input token <uyezds> is not in the model. Will return None type vector
Input token <Aurangezeb> is not in the model. Will return None type vector
Input token <Girsa> is not in the model. Will return None type vector
Input token <Zil-Hijja> is not in the model. Will return None type vector
Input token <Brahmdev> is not in the model. Will return None type vector
Input token <witness-spouse> is not in the model. Will return None type vector
Input token <party-spouse> is not in the model. Will return None type vector
Input token <Logoplaste> is not in the model. Will return None type vector
Input token <Logoplaste> is not in the model. Will return None type vector
Input token <Maiorem> is not in the model. Will return None type vector
Input token <Pikiran> is not in the model. Will return None type vector
Input token <Pikiran> is not in the mode

...

Input token <ReST-friendly> is not in the model. Will return None type vector
Input token <Kiteenjärvi> is not in the model. Will return None type vector
Input token <Chondrostoma> is not in the model. Will return None type vector
Input token <Ryomo> is not in the model. Will return None type vector
Input token <TI-05> is not in the model. Will return None type vector
Input token <Polycratia> is not in the model. Will return None type vector
Input token <Sergozero> is not in the model. Will return None type vector
Input token <Nyboe> is not in the model. Will return None type vector
Input token <Sennheim> is not in the model. Will return None type vector
Input token <Riksmål> is not in the model. Will return None type vector
Input token <Rykkinn> is not in the model. Will return None type vector
Input token <Jeverland> is not in the model. Will return None type vector
Input token <Étienne-François> is not in the model. Will return None type vector
Input token <Montaignac> is not in the

Input token <Federàl> is not in the model. Will return None type vector
Input token <Büyükçekmece> is not in the model. Will return None type vector
Input token <Gruzenberg> is not in the model. Will return None type vector
Input token <Spätrot-Rotgipfler> is not in the model. Will return None type vector
Input token <Newermind> is not in the model. Will return None type vector
Input token <D'Ocon> is not in the model. Will return None type vector
Input token <Yauyos> is not in the model. Will return None type vector
Input token <vicugnas> is not in the model. Will return None type vector
Input token <Anti-Bases> is not in the model. Will return None type vector
Input token <Tangimoana> is not in the model. Will return None type vector
Input token <Foxland> is not in the model. Will return None type vector
Input token <Multi-Academy> is not in the model. Will return None type vector
Input token <Foxland> is not in the model. Will return None type vector
Input token <盲拳> is not in the m

Input token <TranzCoastal> is not in the model. Will return None type vector
Input token <Chilkalguda> is not in the model. Will return None type vector
Input token <Al-Kausar> is not in the model. Will return None type vector
Input token <Umachandra> is not in the model. Will return None type vector
Input token <Subrahmanyaswamy> is not in the model. Will return None type vector
Input token <107J> is not in the model. Will return None type vector
Input token <Lingampally> is not in the model. Will return None type vector
Input token <Paxhill> is not in the model. Will return None type vector
Input token <U-86> is not in the model. Will return None type vector
Input token <Poslaću> is not in the model. Will return None type vector
Input token <Jašar> is not in the model. Will return None type vector
Input token <balticus> is not in the model. Will return None type vector
Input token <family/youth> is not in the model. Will return None type vector
Input token <Sanctifica> is not in the 

Input token <Drono> is not in the model. Will return None type vector
Input token <WVBL-LP> is not in the model. Will return None type vector
Input token <oralities> is not in the model. Will return None type vector
Input token <Couch-Stone> is not in the model. Will return None type vector
Input token <79093> is not in the model. Will return None type vector
Input token <BSk> is not in the model. Will return None type vector
Input token <Au-Berneck> is not in the model. Will return None type vector
Input token <0.330000> is not in the model. Will return None type vector
Input token <Kagina> is not in the model. Will return None type vector
Input token <HONOReform> is not in the model. Will return None type vector
Input token <HONOReform> is not in the model. Will return None type vector
Input token <Kanengoni> is not in the model. Will return None type vector
Input token <Saranggola> is not in the model. Will return None type vector
Input token <Þórdís> is not in the model. Will retur

Input token <Over-Mind> is not in the model. Will return None type vector
Input token <OM660> is not in the model. Will return None type vector
Input token <OM660> is not in the model. Will return None type vector
Input token <-LSB-> is not in the model. Will return None type vector
Input token <Bogatyanovskiy> is not in the model. Will return None type vector
Input token <Sobornaya> is not in the model. Will return None type vector
Input token <BAHAUDIN> is not in the model. Will return None type vector
Input token <BAHAUDIN> is not in the model. Will return None type vector
Input token <BOSAN> is not in the model. Will return None type vector
Input token <Front-Pak> is not in the model. Will return None type vector
Input token <legislative/national> is not in the model. Will return None type vector
Input token <Dotaku-shaped> is not in the model. Will return None type vector
Input token <Kamikoma> is not in the model. Will return None type vector
Input token <Plocamium> is not in the

In [14]:
# num of sentences in filtered data split vs. num of sentences after filtering out with Glove
print(num_sentences_tr_flt, len(idx_sent_filtered_tr))
print(num_sentences_dv_flt, len(idx_sent_filtered_dv))
print(num_sentences_ts_flt, len(idx_sent_filtered_ts))

214804 174061
28148 22752
30134 24412


In [15]:
# ========================= make dataset input ==========================

In [16]:
def LoadFilterIdxFile(filteridx_filename:str):
    with open(filteridx_filename, 'r', encoding='utf-8') as textfile:
        idx_filter = json.load(textfile)
    return idx_filter

In [17]:
#idx_filter = LoadFilterIdxFile('./dataset_filtered/dev_idx_filtered.txt')

In [18]:
def LoadPosInfo(pos_dir:str, split_name:str, idx_to_keep:list):
    print('\tloading POS info...')
    total_num_sent_after_trans = 0
    sent_idx_to_noun_idx_mapping = dict(zip(idx_to_keep, [[] for i in range(len(idx_to_keep))]))
    with os.scandir(pos_dir) as it:
        for entry in it:
            if entry.name.startswith(split_name): # load all pos info with given split name
                with open(entry.path, 'r', encoding='utf-8') as textfile:
                    pos_info = json.load(textfile)
                    for (sent_idx, sent_pos) in pos_info.items():
                        sent_idx = int(sent_idx)
                        if sent_idx in idx_to_keep: # ignore sentences based on idx filter
                            for token_pos in sent_pos:
                                if token_pos['pos'] == 'NN' or token_pos['pos'] == 'NNS':
                                    # only care for NN and NNS for now, ignore pronouns NNP
                                    # the token index given by stanford pos starts with 1 in a sent
                                    token_idx = token_pos['index'] - 1
                                    sent_idx_to_noun_idx_mapping[sent_idx].append(token_idx)
                                    
    with open('sent_idx_to_noun_idx_mapping_filtered_{}.json'.format(split_name), 'w', encoding='utf-8') as textfile:
        json.dump(sent_idx_to_noun_idx_mapping, textfile)
    
    if split_name == 'train':
        # estimate num of sentences after limiting one noun per sentence
        for value in sent_idx_to_noun_idx_mapping.values():
            if not len(value) == 0: 
                total_num_sent_after_trans += len(value)
        print('\tapprox. number of sentences after noun transformation in {} set: {}'.format(split_name, total_num_sent_after_trans))
    else:
        print('\tapprox. number of sentences after noun transformation in {} set: {}'.format(split_name, len(idx_to_keep)))
    
    return sent_idx_to_noun_idx_mapping

In [19]:
#sent_idx_to_noun_idx_mapping = LoadPosInfo('./dataset_pos', 'dev', idx_filter)

In [20]:
########## ============ filter out a certain noun? ================
# rank the number of nouns, go through the whole test set and find highest freq. noun
# take out those sentences (make sure also in filtered idx)
# create an additional file for those nouns as new test.noun

In [21]:
def FilterHighFreqNoun(pos_dir:str, split_name:str, idx_to_keep:list):
    print('\tchecking highest freq noun...')
    total_num_sent_noun1 = 0
    noun_to_sent_idx_mapping = dict()
    
    with os.scandir(pos_dir) as it:
        for entry in it:
            if entry.name.startswith(split_name): # load all pos info with given split name
                with open(entry.path, 'r', encoding='utf-8') as textfile:
                    pos_info = json.load(textfile)
                    for (sent_idx, sent_pos) in pos_info.items():
                        sent_idx = int(sent_idx)
                        if sent_idx in idx_to_keep: # ignore sentences based on idx filter
                            for token_pos in sent_pos:
                                if token_pos['pos'] == 'NN' or token_pos['pos'] == 'NNS':
                                    # only care for NN and NNS for now, ignore pronouns NNP
                                    # the token index given by stanford pos starts with 1 in a sent
                                    word = token_pos['word']
                                    token_idx = token_pos['index'] - 1
                                    if not word in noun_to_sent_idx_mapping:
                                        noun_to_sent_idx_mapping[word] = list()
                                    noun_to_sent_idx_mapping[word].append([sent_idx, token_idx])
    
    # filter out the noun with the most frequent appearance from sorting
    sorted_noun_to_sent_idx_mapping = sorted(noun_to_sent_idx_mapping.items(), key=lambda x: len(x[1]), reverse=True)
    noun_to_sent_idx_mapping = dict()
    sent_idx_filter = list()
    sent_idx_to_noun_idx_mapping = dict()
    
    for i in range(10):
        highfreq_noun = sorted_noun_to_sent_idx_mapping[i][0]
        highfreq_position = sorted_noun_to_sent_idx_mapping[i][1]
        for (sent_idx, noun_idx) in highfreq_position:
            if sent_idx not in sent_idx_filter:
                sent_idx_filter.append(sent_idx)
                sent_idx_to_noun_idx_mapping[sent_idx] = list()
            sent_idx_to_noun_idx_mapping[sent_idx].append(noun_idx)
        noun_to_sent_idx_mapping[highfreq_noun] = highfreq_position
    
    with open('top10noun_with_idx.json', 'w', encoding='utf-8') as textfile:
        json.dump(noun_to_sent_idx_mapping, textfile)
    
    return noun_to_sent_idx_mapping.keys(), sent_idx_filter, sent_idx_to_noun_idx_mapping

In [22]:
#highfreq_noun, sent_idx_filter, sent_idx_to_noun_idx_mapping = FilterHighFreqNoun('./dataset_pos', 'train', idx_filter)

In [23]:
def LoadSentenceFile(sent_filename:str, idx_to_keep:list):
    print('\tloading sentences from file...')
    idx_to_sentences_mapping = dict(zip(idx_to_keep, [[] for i in range(len(idx_to_keep))]))
    with open(sent_filename, 'r', encoding='utf-8') as textfile:
        sentences = json.load(textfile)
        for sent_idx, sent in enumerate(sentences):
            if sent_idx in idx_to_keep:
                sent = sent.split()
                
                for i in range(len(sent)):
                    if sent[i] == '-RCB-':
                        sent[i] = ')'
                    elif sent[i] == '-LCB-':
                        sent[i] = '('
                        
                idx_to_sentences_mapping[sent_idx] = sent
            
    return idx_to_sentences_mapping

In [24]:
#idx_to_sentences_mapping = LoadSentenceFile('./dataset_filtered/dev.json', idx_filter)

In [25]:
# pad sentences if it's not enough length
def Padding(sent:list, max_len:int, embedding_dim:int):
    padded = np.zeros((max_len, embedding_dim))
    if len(sent) < max_len: # when the sentence is shorter then the longest sent in set
        padded[:len(sent)] = sent
    return padded

In [26]:
def RandomSampleTokenIdx(list_of_idx_to_mask:list):
    if len(list_of_idx_to_mask) == 1:
        return list_of_idx_to_mask
    return list(np.random.choice(list_of_idx_to_mask, 1))

In [27]:
def Masking(noun_idx:int, sent:list, embedding_dim:int):
    sent[noun_idx] = np.zeros(embedding_dim)
    return sent

In [28]:
# for sentence with more than one noun, repeat and interchange the noun to be masked 
def SentToEmbedding(idx_to_sentence_mapping:dict, sent_idx_to_noun_idx_mapping:dict, glove_model, embedding_dim:int, max_len:int, split_name:str):
    print('\tconverting sentences to embeddings...')
    sentence_embeddings = list() # sentence embedding [300d, 300d, 300d]
    label_embeddings = list() # label embedding 300d
    label_positions = list() # label position in the sentence
    for (sent_idx, sentence) in idx_to_sentence_mapping.items():
        if not len(sent_idx_to_noun_idx_mapping[sent_idx]) == 0: # if no nouns in the current sentence, skip
            sent = list()
            for token in sentence:
                token_embedding = glove_model.get_vector(token)
                sent.append(token_embedding)
            
            if split_name != 'train': # if not training set, random sample a noun from the sent to mask
                noun_indices = RandomSampleTokenIdx(sent_idx_to_noun_idx_mapping[sent_idx])
            else: # if training set, mask nouns based on indices, mask one noun per sent
                noun_indices = sent_idx_to_noun_idx_mapping[sent_idx]
            
            for noun_idx in noun_indices:
                label_embeddings.append(sent[noun_idx]) # save label embedding
                label_positions.append(noun_idx) # save label index in the sentence
                sent = Masking(noun_idx, sent, embedding_dim) # mask noun at given position
                sent = Padding(sent, max_len, embedding_dim) # add padding with 300d 0s to the end
                sentence_embeddings.append(sent)

    return sentence_embeddings, label_embeddings, label_positions

In [29]:
#embedding_dim = 300
#max_len = int(mean_total + std_total)
#sentence_embeddings, label_embeddings, label_positions = SentToEmbedding(idx_to_sentences_mapping, sent_idx_to_noun_idx_mapping glove_model, embedding_dim, max_len, 'dev')
#print(np.shape(sentence_embeddings))
#print(np.shape(label_embeddings))
#print(np.shape(label_positions))

In [32]:
# create a custom dataset for dataloader to use
class WikiDataset(Dataset):
    def __init__(self, dataset, labels, label_positions):
        self.dataset = dataset
        self.labels = labels
        self.label_positions = label_positions
    
    def __len__(self):
        return len(self.labels)
    
    def __getitem__(self, idx):
        datapoint = self.dataset[idx]
        label = self.labels[idx]
        label_position = self.label_positions[idx]
        return datapoint, label, label_position

In [33]:
#### change the input to dataloader to sentence themselves
#### move embedding retrieval to withint dataset class 

class WikiDatasetNew(Dataset):
    def __init__(self, dataset, labels, label_positions):
        self.dataset = dataset
        self.labels = labels
        self.label_positions = label_positions
    
    def __len__(self):
        return len(self.labels)
    
    def __getitem__(self, idx):
        datapoint = self.dataset[idx]
        label = self.labels[idx]
        label_position = self.label_positions[idx]
        return datapoint, label, label_position

In [34]:
#data = WikiDataset(sentence_embeddings, label_embeddings, label_positions)
#loader = DataLoader(dataset=data, shuffle=False, pin_memory=False, batch_size=512)
#it = iter(loader)
#x,y,nidx =  next(it)
#print(x.shape)
#print(x.dtype)
#print(y.shape)
#print(y.dtype)
#print(nidx.shape)
#print(nidx.dtype)

In [35]:
def MakeDataloader(filteridx_filename:str, sent_filename:str, pos_dir:str, split_name:str, glove_model, embedding_dim:int, max_len:int, batch_size:int, num_workers:int):
    print('making data loader for {} split'.format(split_name))
    idx_to_keep = LoadFilterIdxFile(filteridx_filename)
    sent_idx_to_noun_idx_mappping = LoadPosInfo(pos_dir, split_name, idx_to_keep)
    idx_to_sentence_mapping = LoadSentenceFile(sent_filename, idx_to_keep)
    sentence_embeddings, label_embeddings, label_positions = SentToEmbedding(idx_to_sentence_mapping, sent_idx_to_noun_idx_mapping, glove_model, embedding_dim, max_len, split_name)
    data = WikiDataset(sentence_embeddings, label_embeddings, label_positions)
    
    print('\tfinalizing making data loader')
    
    if split_name == 'test':
        if_shuffle = False
    else:
        if_shuffle = True
        
    # NOTE: for gpu usage, do not use num_workers, turn pin_memory to True
    loader = DataLoader(dataset=data, batch_size=batch_size, shuffle=if_shuffle, num_workers=num_workers, pin_memory=False) 
    
    return loader

In [40]:
def MakeDataloaderNoun(filteridx_filename:str, sent_filename:str, pos_dir:str, split_name:str, glove_model, embedding_dim:int, max_len:int, batch_size:int, num_workers:int):
    print('making data loader for {} split'.format(split_name))
    idx_to_keep = LoadFilterIdxFile(filteridx_filename)
    nouns, sent_idx_filter, sent_idx_to_noun_idx_mapping = FilterHighFreqNoun(pos_dir, split_name, idx_to_keep)
    idx_to_sentence_mapping = LoadSentenceFile(sent_filename, sent_idx_filter)
    sentence_embeddings, label_embeddings, label_positions = SentToEmbedding(idx_to_sentence_mapping, sent_idx_to_noun_idx_mapping, glove_model, embedding_dim, max_len, split_name)
    data = WikiDataset(sentence_embeddings, label_embeddings, label_positions)
    
    print('\tfinalizing making data loader, num sentences in loader: {}'.format(len(label_positions)))
    
    if split_name == 'test':
        if_shuffle = False
    else:
        if_shuffle = True
        
    # NOTE: for gpu usage, do not use num_workers, turn pin_memory to True
    loader = DataLoader(dataset=data, batch_size=batch_size, shuffle=if_shuffle, num_workers=num_workers, pin_memory=False) 
    
    return loader

In [41]:
# sample noun from train
split_name = 'train'
filter_path = './dataset_filtered/{}_idx_filtered.txt'.format(split_name)
file_path = './dataset_filtered/{}.json'.format(split_name)
pos_dir = './dataset_pos'
embedding_dim = 300
batch_size = 128
num_workers = 1
max_len = int(22.514047250226433 + 14.624483763629705)
nounloader = MakeDataloaderNoun(filter_path, file_path, pos_dir, split_name, glove_model, embedding_dim, max_len, batch_size, num_workers)
print(len(nounloader))

making data loader for train split
	checking highest freq noun...
	loading sentences from file...
	converting sentences to embeddings...
	finalizing making data loader, num sentences in loader: 28904
226


In [30]:
# test make dataloader with dev
split_name = 'dev'
filter_path = './dataset_filtered/{}_idx_filtered.txt'.format(split_name)
file_path = './dataset_filtered/{}.json'.format(split_name)
pos_dir = './dataset_pos'
embedding_dim = 300
batch_size = 512
num_workers = 1
max_len = int(mean_total + std_total)
loader = MakeDataloader(filter_path, file_path, pos_dir, split_name, glove_model, embedding_dim, max_len, batch_size, num_workers)
print(len(loader))

making data loader for dev split
	loading POS info...
	approx. number of sentences after noun transformation in dev set: 22752
	loading sentences from file...
	converting sentences to embeddings...
	finalizing making data loader
43


In [31]:
# ================= training =====================

In [87]:
import torch
import torch.optim as optim
import torch.nn as nn
from lstm_model import LSTM

torch.manual_seed(32) # use random seeding

In [88]:
embedding_dim = 300
hidden_dim = 128
num_epochs = 30
num_batches = len(loader)

model = LSTM(embedding_dim=embedding_dim, hidden_dim=hidden_dim)
model = model.double()
loss_function = nn.CosineEmbeddingLoss()
optimizer = optim.Adam(model.parameters(), lr=0.05) # add learning rate decay later
batch_loss = np.zeros(num_batches)
avg_epoch_loss = np.zeros(num_epochs)
best_model_loss = 99999

In [89]:
for epoch in range(num_epochs): # number of epochs
    print('training epoch: {}...'.format(epoch+1))
    for batch_idx, (data, target, target_idx) in enumerate(loader):
        
        # clear out gradients at each batch so pytorch does not accumulates it
        optimizer.zero_grad()
        
        # get current batch_size, remember that most batch has size 512 but some do not
        batch_size = target.shape[0]
        
        # forward pass
        prediction = model(data, target_idx)
        
        # compute loss and gradients, update parameters by optim.step()
        mask = torch.ones(batch_size)
        loss = loss_function(prediction, target, mask)
        loss.backward()
        optimizer.step()
        
        # save batch loss (avg batch loss of all datapoints in batch, automatically obtained from loss)
        batch_loss[batch_idx] = loss
        if (batch_idx + 1) % 50 == 0 or (batch_idx + 1) == num_batches:
            print('\ttrained {}% of epoch {}, current batch loss: {}'.format(round((batch_idx+1)/num_batches*100, 2), epoch+1, loss))
    
    # compute average epoch loss (avg loss of all batches in the epoch)
    avg_epoch_loss[epoch] = np.mean(batch_loss)
    batch_loss = np.zeros(num_batches) # reset the batch loss
    if best_model_loss > avg_epoch_loss[epoch]:
        best_model_loss = avg_epoch_loss[epoch]
        torch.save(model.state_dict(), 'wiki_model.best.pt')
        print('\tsaving best model at epoch {}'.format(epoch))
    
    print('\tfinished training epoch: {}, average loss: {}'.format(epoch+1, avg_epoch_loss[epoch]))

with open('loss_per_epoch.txt', 'w', encoding='utf-8') as textfile:
    for ls in avg_epoch_loss:
        textfile.write('{}\n'.format(ls))

training epoch: 1...
	trained 100.0% of epoch 1, current batch loss: 0.6002731569877698
	saving best model at epoch 0
	finished training epoch: 1, average loss: 0.6857085827696457


In [ ]:
# =========== write testing here! ================

In [ ]:
def Top10Hit(prediction, label=str, glove_model):
    top10hit = glove_model.most_similar_embedding(prediction, topn=10, ignore_similarity=True) # sorted list of tokens
    if label in top10hit:
        idxtop10 = top10hit.index(label) + 1
        return idxtop10 # if label is in top 10 hit, return the position in top10
    return False

In [85]:
# make test data loader
split_name = 'test'
filter_path = './dataset_filtered/{}_idx_filtered.txt'.format(split_name)
file_path = './dataset_filtered/{}.json'.format(split_name)
pos_dir = './dataset_pos'
embedding_dim = 300
batch_size = 1
num_workers = 2
max_len = int(mean_total + std_total)
testloader = MakeDataloader(filter_path, file_path, pos_dir, split_name, glove_model, embedding_dim, max_len, batch_size, num_workers)
num_testdata = len(testloader)
print(num_testdata)

making data loader for test split
	loading POS info...
	approx. number of sentences after noun transformation in test set: 24412
	loading sentences from file...
	converting sentences to embeddings...
	finalizing making data loader
23197


In [95]:
model_path = './wiki_model.best.pt'
model = LSTM(embedding_dim=embedding_dim, hidden_dim=hidden_dim)
model.load_state_dict(torch.load(model_path))
model = model.eval() # set model to eval mode

avg_similarity = 0 # compute the avg similarity between each label and predictions
num_top10hit = 0 # compute number of top10hit predictions
avg_top10hit_position = 0 # compute the avg positions in top10 hit, if hit
num_top1hit = 0 # compute number of top1hit predictions

In [ ]:
######## change the target in testing loader to string target 
with torch.no_grad():
    for data_idx, (data, target, target_idx) in enumerate(testloader):
        prediction = model(data, target_idx)
        
        # compute avg similarity between prediction and target (the closer to 1 the better)
        similarity = glove_model.similarity(prediction, taget)
        avg_similarity += similarity
        
        # compute top 10 hit of the prediction 
        top10idx = Top10Hit(prediction, target, glove_model)
        if top10idx:
            num_top10hit += 1
            avg_top10hit_position += top10idx
        
            # compute top 1 hit of the prediction 
            if top10idx == 1:
                num_top1hit += 1

avg_similarity = avg_similarity / num_testdata
avg_top10hit_position = avg_top10hit_position / num_top10hit

In [ ]:
print('average similarity of test set: {}'.format(avg_similarity))
print('accuracy of top 1 hit: {}/{}, {}%'.format(num_top1hit, num_testdata, round(num_top1hit/num_testdata*100, 2)))
print('accuracy of top 10 hit: {}/{}, {}%'.format(num_top10hit, num_testdata, round(num_top10hit/num_testdata*100, 2)))
print('average position of top 10 hit on a scale from 1 to 10: {}'.format(avg_top10hit_position))

In [ ]:
# ================= random playground ===============

In [74]:
#### https://discuss.pytorch.org/t/example-of-many-to-one-lstm/1728
#### example LSTM input format (timestamp/sent_len, batch_size, embedding_size)
#### many to one example
#### lookup usage for batch_first parameter to have (batch_size, timestamp, embedding_size)
import torch
import torch.nn as nn
from torch.autograd import Variable

time_steps = 10
batch_size = 3
in_size = 5
hidden_size = 7

model = nn.LSTM(in_size, hidden_size, num_layers=1, batch_first=True, bidirectional=True)
linear1 = nn.Linear(hidden_size, in_size)
input_seq = Variable(torch.randn(batch_size, time_steps, in_size))
output_seq, hidden = model(input_seq)
output = output_seq[[0, 1, 2], [0, 0, 0]] # change index here
output = torch.mean(output.view(3, 2, 7), dim=1)
output = linear1(output)

loss = nn.CosineEmbeddingLoss()
target = Variable(torch.randn(batch_size, in_size))
err = loss(output, target, torch.ones(batch_size))
#err.backward()

In [75]:
print(input_seq.shape)
#print(input_seq)
print(output.shape)
print(output)
print(target.shape)
#print(target)
print(err)

torch.Size([3, 10, 5])
torch.Size([3, 5])
tensor([[ 0.2934, -0.1371, -0.1866,  0.2318,  0.3225],
        [ 0.1928, -0.1855, -0.1669,  0.2161,  0.3401],
        [ 0.2074, -0.1780, -0.1629,  0.2111,  0.3307]],
       grad_fn=<AddmmBackward>)
torch.Size([3, 5])
tensor(0.8353, grad_fn=<MeanBackward0>)


In [76]:
noun_idx = torch.randint(0, 10, (3,)) # position of the target word
batch_idx = torch.arange(output_seq.shape[0]) # sent idx in batch
print(noun_idx)
print(batch_idx)
print(output_seq.shape)
test = output_seq[batch_idx, noun_idx] # to get a particular position from time stamp out from the batche first method
print(test.shape)
print(test)
print(test.view(3, 2, 7))
print(torch.mean(test.view(3, 2, 7), dim=1))

tensor([3, 8, 5])
tensor([0, 1, 2])
torch.Size([3, 10, 14])
torch.Size([3, 14])
tensor([[ 0.0143,  0.0745,  0.0758,  0.0042,  0.0181, -0.0925, -0.1477,  0.1347,
         -0.1398, -0.2290, -0.1909,  0.2565, -0.0859,  0.0152],
        [-0.1170, -0.0436,  0.1290, -0.0768, -0.1193,  0.1028,  0.0426, -0.0431,
          0.0380, -0.0869, -0.2066,  0.2715, -0.2567,  0.0138],
        [-0.2574,  0.0803,  0.0571, -0.1203, -0.1661,  0.0448,  0.0889, -0.0884,
         -0.0417, -0.2822, -0.1843,  0.3771, -0.1820,  0.2089]],
       grad_fn=<IndexBackward>)
tensor([[[ 0.0143,  0.0745,  0.0758,  0.0042,  0.0181, -0.0925, -0.1477],
         [ 0.1347, -0.1398, -0.2290, -0.1909,  0.2565, -0.0859,  0.0152]],

        [[-0.1170, -0.0436,  0.1290, -0.0768, -0.1193,  0.1028,  0.0426],
         [-0.0431,  0.0380, -0.0869, -0.2066,  0.2715, -0.2567,  0.0138]],

        [[-0.2574,  0.0803,  0.0571, -0.1203, -0.1661,  0.0448,  0.0889],
         [-0.0884, -0.0417, -0.2822, -0.1843,  0.3771, -0.1820,  0.2089]]],
  

In [ ]:
#### https://discuss.pytorch.org/t/how-to-retrieve-the-sample-indices-of-a-mini-batch/7948/12
#### mini batch example 
for batch_idx, (data, target, idx) in enumerate(loader):
    print('Batch idx {}, dataset index {}'.format(
        batch_idx, idx))

In [ ]:
#### https://discuss.pytorch.org/t/correctly-feeding-lstm-with-minibatch-time-sequence-data/52101/2
#### batch_first example

In [ ]:
#### always look at torch documentation https://pytorch.org/docs/stable/nn.html

In [ ]:
# NOTE: bidirectional lstm will output 2x the hidden size
# reshape, get prediction from both forward and backward process, avg out the prediction???

In [83]:
import torch.nn.functional as F

test1 = Variable(torch.randn(batch_size, in_size))
print(test1)
test2 = F.normalize(test1, dim=1)
print(test2)
for t in test2:
    print(np.linalg.norm(t))

tensor([[ 0.3917,  0.7974, -0.2882,  1.3368, -0.5921],
        [ 1.1710,  0.9337, -1.0539, -0.4907,  0.7063],
        [ 0.9793,  0.0461, -1.1660,  2.3212, -1.0903]])
tensor([[ 0.2258,  0.4596, -0.1661,  0.7705, -0.3413],
        [ 0.5788,  0.4615, -0.5209, -0.2425,  0.3491],
        [ 0.3283,  0.0155, -0.3909,  0.7782, -0.3655]])
1.0
0.9999999
1.0
